In [51]:
import pandas as pd

In [1]:
target_lang="ga-IE"  # change to your target lang

In [101]:
from datasets import load_dataset

# dataset = load_dataset("mozilla-foundation/common_voice_8_0", 
#                        "ga-IE", 
#                        split="train", 
#                        use_auth_token = True)

dataset = load_dataset("opus_dgt", lang1="ga", lang2="pl", split = 'train')

Using custom data configuration ga-pl-lang1=ga,lang2=pl
Reusing dataset opus_dgt (/workspace/cache/hf/datasets/opus_dgt/ga-pl-lang1=ga,lang2=pl/0.0.0/a4db75cea3712eb5d4384f0539db82abf897c6b6da5e5e81693e8fd201efc346)


In [102]:
# ga_txt = [i['ga'] for i in dataset['translation']]
# ga_txt = pd.Series(ga_txt)

In [103]:
chars_to_ignore_regex = '[,?.!\-\;\:"“%‘”�—’…–]'  # change to the ignored characters of your fine-tuned model

In [107]:
import re

def extract_text(batch):
  text = batch["translation"]
  ga_text = text['ga']
  batch["text"] = re.sub(chars_to_ignore_regex, "", ga_text.lower())
  return batch

In [108]:
dataset = dataset.map(extract_text, remove_columns=dataset.column_names)

0ex [00:00, ?ex/s]

In [112]:
dataset.push_to_hub(f"{target_lang}_opus_dgt_train", split="train")

Pushing dataset shards to the dataset hub:   0%|          | 0/1 [00:00<?, ?it/s]

## N-gram KenLM

In [116]:
from datasets import load_dataset

dataset = load_dataset("jcmc/ga-IE_opus_dgt_train", split="train")

with open("text.txt", "w") as file:
  file.write(" ".join(dataset["text"]))

Downloading:   0%|          | 0.00/1.60k [00:00<?, ?B/s]

Using custom data configuration jcmc--ga-IE_opus_dgt_train-aa318da91f5f84f6


  0%|          | 0/1 [00:00<?, ?it/s]

Downloading:   0%|          | 0.00/12.7M [00:00<?, ?B/s]

  0%|          | 0/1 [00:00<?, ?it/s]

Dataset parquet downloaded and prepared to /workspace/cache/hf/datasets/parquet/jcmc--ga-IE_opus_dgt_train-aa318da91f5f84f6/0.0.0/1638526fd0e8d960534e2155dc54fdff8dce73851f21f031d2fb9c2cf757c121. Subsequent calls will reuse this data.


In [118]:
!../kenlm/build/bin/lmplz -o 5 <"text.txt" > "5gram.arpa"

=== 1/5 Counting and sorting n-grams ===
Reading /workspace/wav2vec-1b-cv8-ir/text.txt
----5---10---15---20---25---30---35---40---45---50---55---60---65---70---75---80---85---90---95--100
****************************************************************************************************
Unigram tokens 4378228 types 70781
=== 2/5 Calculating and sorting adjusted counts ===
Chain sizes: 1:849372 2:14475680768 3:27141902336 4:43427041280 5:63331106816
Statistics:
1 70780 D1=0.684187 D2=1.0538 D3+=1.37643
2 652306 D1=0.766205 D2=1.12085 D3+=1.39031
3 1669326 D1=0.84217 D2=1.20654 D3+=1.39941
4 2514789 D1=0.896214 D2=1.29731 D3+=1.47431
5 3053088 D1=0.794858 D2=1.47897 D3+=1.5117
Memory estimate for binary LM:
type     MB
probing 164 assuming -p 1.5
probing 192 assuming -r models -p 1.5
trie     77 without quantization
trie     42 assuming -q 8 -b 8 quantization 
trie     69 assuming -a 22 array pointer compression
trie     34 assuming -a 22 -q 8 -b 8 array pointer compression and quantiza

In [122]:
with open("5gram.arpa", "r") as read_file, open("5gram_correct.arpa", "w") as write_file:
  has_added_eos = False
  for line in read_file:
    if not has_added_eos and "ngram 1=" in line:
      count=line.strip().split("=")[-1]
      write_file.write(line.replace(f"{count}", f"{int(count)+1}"))
    elif not has_added_eos and "<s>" in line:
      write_file.write(line)
      write_file.write(line.replace("<s>", "</s>"))
      has_added_eos = True
    else:
      write_file.write(line)

In [123]:
!head -20 5gram_correct.arpa

\data\
ngram 1=70781
ngram 2=652306
ngram 3=1669326
ngram 4=2514789
ngram 5=3053088

\1-grams:
-5.8501472	<unk>	0
0	<s>	-0.11565505
0	</s>	-0.11565505
-5.4088216	miontuairisc	-0.20133564
-4.6517477	cheartaitheach	-0.24842946
-2.1893916	maidir	-1.7147961
-2.1071756	le	-0.7007309
-4.156014	coinbhinsiún	-0.31064242
-1.8876181	ar	-0.9045828
-4.62287	dhlínse	-0.24268326
-1.6051095	agus	-0.8729715
-4.1465816	aithint	-0.21693327


In [124]:
from transformers import AutoProcessor

processor = AutoProcessor.from_pretrained("./")

In [125]:
vocab_dict = processor.tokenizer.get_vocab()
sorted_vocab_dict = {k.lower(): v for k, v in sorted(vocab_dict.items(), key=lambda item: item[1])}

In [126]:
from pyctcdecode import build_ctcdecoder

decoder = build_ctcdecoder(
    labels=list(sorted_vocab_dict.keys()),
    kenlm_model_path="5gram_correct.arpa",
)

Found entries of length > 1 in alphabet. This is unusual unless style is BPE, but the alphabet was not recognized as BPE type. Is this correct?
Unigrams and labels don't seem to agree.


In [127]:
from transformers import Wav2Vec2ProcessorWithLM

processor_with_lm = Wav2Vec2ProcessorWithLM(
    feature_extractor=processor.feature_extractor,
    tokenizer=processor.tokenizer,
    decoder=decoder
)

In [128]:
from huggingface_hub import Repository

repo = Repository(local_dir="./", clone_from="jcmc/wav2vec-1b-cv8-ir")

/workspace/wav2vec-1b-cv8-ir/./ is already a clone of https://huggingface.co/jcmc/wav2vec-1b-cv8-ir. Make sure you pull the latest changes with `repo.git_pull()`.


In [129]:
pwd

'/workspace/wav2vec-1b-cv8-ir'

In [ ]:
processor_with_lm.save_pretrained("xls-r-300m-sv")